In [1]:
# pip install fuzzywuzzy

## Package Load

In [2]:
import pandas as pd
import json
from collections import Counter
from fuzzywuzzy import process
from bs4 import BeautifulSoup
import os
import base64
import re
import pprint
import ast
import re

/Users/than/anaconda3/envs/mids/lib/python3.12/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


## Use this section to import files from Google Drive

In [3]:
# from google.colab import drive
# drive.mount('/content/drive')

In [4]:
# # Set Variable so that the rest of code works
# imported_files_from_Gdrive = True

# #cleaned = '/content/drive/MyDrive/Colab Notebooks/DATASCI 207/data/first_500_rows_cleaned.csv'
# #items = '/content/drive/MyDrive/Colab Notebooks/DATASCI 207/data/items.csv'
# tags = '/content/drive/MyDrive/tags.csv'

## Use this below section to Import from your Computer Directory
Use case members: Taylor 

In [5]:
# Set Variable so that the rest of code works
imported_files_from_Gdrive = False

# Get the current working directory
cwd = os.getcwd()
print(f"Current Working Directory is: {cwd}")

# Define relative file paths and their respective DataFrame names
file_paths = {
    "desc_df": 'data/desc_0.csv.gz',
    "tag_df": 'data/tags.csv.gz',
    "items_df": 'data/items.csv.gz'
}

# Iterate over the file paths dictionary
for df_name, rel_path in file_paths.items():
    full_path = os.path.join(cwd, rel_path)
    print(f"Full File Path for {df_name.replace('df_', '').capitalize()} Data is: {full_path}")
    
    if os.path.exists(full_path):
        print(f"{df_name.replace('df_', '').capitalize()} file exists, proceeding to read the file.")
        globals()[df_name] = pd.read_csv(full_path, compression='gzip', nrows=5000)
        print(globals()[df_name])
    else:
        print(f"File does not exist. Please check the file path for {df_name.replace('df_', '').capitalize()} Data.")

Current Working Directory is: /Users/than/uc_berkeley/courses/207/final_project
Full File Path for Desc_df Data is: /Users/than/uc_berkeley/courses/207/final_project/data/desc_0.csv.gz
Desc_df file exists, proceeding to read the file.
      RECORD_ID                                          ITEM_DESC
0             2  PCEtLSBEZXNjVGVtcGxhdGVJRDogRWxlY3RyaWNhbCAoNj...
1             3  CiAgPCFET0NUWVBFIGh0bWw+CjxodG1sIGxhbmc9ImVuIj...
2            15  PGh0bWwgbGFuZz0iZW4iPjxoZWFkPjxtZXRhIGNoYXJzZX...
3            24  PGh0bWwgbGFuZz0iZW4iPjxoZWFkPjxtZXRhIGNoYXJzZX...
4            30  PCEtLSBEZXNjVGVtcGxhdGVJRDogRWxlY3RyaWNhbCAoNj...
...         ...                                                ...
4995      26751  PCEtLSBEZXNjVGVtcGxhdGVJRDogRWxlY3RyaWNhbCAoNT...
4996      26752  PHN0eWxlIHR5cGU9J3RleHQvY3NzJz4KaHRtbCwgYm9keS...
4997      26753  PGh0bWwgbGFuZz0iZW4iPjxoZWFkPjxtZXRhIGNoYXJzZX...
4998      26755  PCEtLSBEZXNjVGVtcGxhdGVJRDogRWxlY3RyaWNhbCAoNT...
4999      26756  CiAgPGh0bWw

# Tags Data Processing

* If imported from Google Drive, read in the CSV.
* If imported from personal directory, then the data should have been laoded from the code above.


In [6]:
# Load the tags data if imported_files_from_Gdrive is True
if imported_files_from_Gdrive:
    print(f"Reading the Tags Data from Google Drive")
    tag_df = pd.read_csv(tags)
    print(tag_df.shape)
    tag_df.head()
else: 
    print(f"Tags Data was loaded without Google Drive")
    print(tag_df.shape)
    tag_df.head()

Tags Data was loaded without Google Drive
(5000, 2)


### Check the Shape of Tags
Checks for Tags Dataframe

In [7]:
# Ensure 'RECORD_ID' is treated as an integer if it's not already
tag_df['RECORD_ID'] = tag_df['RECORD_ID'].astype(int)

# Get the largest 'RECORD_ID'
max_record_id = tag_df['RECORD_ID'].max()

# Print the result
print(f'The largest RECORD_ID is: {max_record_id}')

The largest RECORD_ID is: 4999


### EDA Tag Data 
* Parseing the _ITEMS_TAGS_ column into columns

In [8]:
df = tag_df[tag_df['RECORD_ID'] < 5000] # Filter the DataFrame
df.loc[:, 'ITEM_TAGS'] = df.loc[:, 'ITEM_TAGS'].apply(json.loads) # Convert the 'ITEM_TAGS' column to a dictionary
df.loc[:, 'ITEM_TAGS'] = df.loc[:, 'ITEM_TAGS'].apply(lambda x: {k: v for i in x for k, v in i.items()}) #  Convert the 'ITEM_TAGS' column to a dictionary
json_cols = pd.json_normalize(df['ITEM_TAGS']) #    Normalize the 'ITEM_TAGS' column
df = pd.concat([df, json_cols], axis=1) #   Concatenate the normalized columns with the original DataFrame
print(df.shape) #    Print the shape of the resulting DataFrame
print(df.columns) #  Print the columns of the resulting DataFrame
df.head() #  Print the first few rows of the resulting DataFrame


(5000, 1744)
Index(['RECORD_ID', 'ITEM_TAGS', 'Brand', 'Bundle Description',
       'Compatible Make', 'Compatible Model', 'Compatible Year', 'Core Charge',
       'Fitment Type', 'Interchange Part Number',
       ...
       'OEM Part Number 4', 'OEM Part Number 5', 'Reference Part Number',
       'Spark Plug Wire Part Number', 'Spark Plug Wire Reference Part Number',
       'California Prop 7294', 'Wiring Harness Length',
       'Noise Suppression Type', 'Package contents:', 'Product description:'],
      dtype='object', length=1744)


RECORD_ID                                          ITEM_TAGS  \
0          0  {'Brand': 'Dayco', 'Bundle Description': '1 pc...   
1          1  {'Brand': 'Toyota', 'DOT Date Code': 'NA', 'In...   
2          2  {'Brand': 'NISSAN', 'Conditions & Options': '8...   
3          3  {'Application': 'Ford Mustang Starter Motor Re...   
4          4  {'Application': 'Mercedes CLK320 Crankcase Bre...   

                     Brand                        Bundle Description  \
0                    Dayco  1 pc Genuine Dayco Radiator Coolant Hose   
1                   Toyota                                       NaN   
2                   NISSAN                                       NaN   
3  Standard Motor Products                                       NaN   
4                     Febi                                       NaN   

  Compatible Make Compatible Model Compatible Year            Core Charge  \
0           Dodge      W100 Series            1967  Free - No Core Charge   
1             NaN              NaN             NaN                    NaN   
2             NaN              NaN             NaN                    NaN   
3             NaN              NaN             NaN                    NaN   
4             NaN              NaN             NaN                    NaN   

         Fitment Type               Interchange Part Number  ...  \
0  Direct Replacement  Gates Bando C541 NAPA CARQUEST 75-64  ...   
1                 NaN                               61050Al  ...   
2                 NaN                             601-10054  ...   
3                 NaN                                   NaN  ...   
4                 NaN                                   NaN  ...   

  OEM Part Number 4 OEM Part Number 5 Reference Part Number  \
0               NaN               NaN                   NaN   
1               NaN               NaN                   NaN   
2               NaN               NaN                   NaN   
3               NaN               NaN                   NaN   
4               NaN               NaN                   NaN   

  Spark Plug Wire Part Number Spark Plug Wire Reference Part Number  \
0                         NaN                                   NaN   
1                         NaN                                   NaN   
2                         NaN                                   NaN   
3                         NaN                                   NaN   
4                         NaN                                   NaN   

  California Prop 7294 Wiring Harness Length Noise Suppression Type  \
0                  NaN                   NaN                    NaN   
1                  NaN                   NaN                    NaN   
2                  NaN                   NaN                    NaN   
3                  NaN                   NaN                    NaN   
4                  NaN                   NaN                    NaN   

  Package contents: Product description:  
0               NaN                  NaN  
1               NaN                  NaN  
2               NaN                  NaN  
3               NaN                  NaN  
4               NaN                  NaN  

[5 rows x 1744 columns]

### Summary of the Tags Dataset

In [9]:
#df.info(verbose=True, show_counts=True)

# Get the non-null count for each column
non_null_counts = df.notnull().sum()

# Sort the columns based on the non-null counts
sorted_columns = non_null_counts.sort_values(ascending=False).index

# Rearrange the DataFrame based on the sorted order
sorted_df = df[sorted_columns]

# Display the sorted DataFrame info
sorted_df.info(verbose=True, show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5000 entries, 0 to 4999
Data columns (total 1744 columns):
 #     Column                                           Non-Null Count  Dtype 
---    ------                                           --------------  ----- 
 0     RECORD_ID                                        5000 non-null   int64 
 1     ITEM_TAGS                                        5000 non-null   object
 2     Brand                                            4990 non-null   object
 3     Manufacturer Part Number                         4512 non-null   object
 4     Manufacturer Warranty                            2701 non-null   object
 5     Type                                             2059 non-null   object
 6     Interchange Part Number                          2014 non-null   object
 7     CS-SKU                                           1438 non-null   object
 8     Part Number                                      1374 non-null   object
 9     Fitment Type   

In [10]:
# Adjust pandas display settings to see full output
pd.set_option('display.max_rows', None)  # Show all rows
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.width', 1000)  # Set the display width to None
pd.set_option('display.max_colwidth', None)  # Set the max column width to None


In [11]:
# Function to tokenize column names
def tokenize_column_names(column_names):
    words = []
    for col in column_names:
        # Split by non-alphanumeric characters
        tokens = re.split(r'\W+', col)
        words.extend(tokens)
    return words

# Tokenize the column names
tokens = tokenize_column_names(df.columns)

# Count the frequency of each token
word_counts = Counter(tokens)

# Create a DataFrame from the word counts
word_counts_df = pd.DataFrame(word_counts.items(), columns=['Word', 'Count'])

# Sort the DataFrame by count in descending order
word_counts_df = word_counts_df.sort_values(by='Count', ascending=False).reset_index(drop=True)

# Display the sorted DataFrame of word counts
print(word_counts_df)

                                 Word  Count
0                                        214
1                              Number    119
2                                Part     98
3                                Type     93
4                            Diameter     70
5                             Fitment     68
6                                  in     56
7                                   2     54
8                                   1     52
9                                  of     48
10                                For     46
11                               Size     44
12                           Included     41
13                                OEM     39
14                           Quantity     39
15                           Material     34
16                             Length     33
17                                  3     32
18                           TechSpec     31
19                                for     31
20                                Fit     29
21        

# Feature Extraction

In [12]:
words = [
    'Year', 'Make', 'Model', 'Manufacturer Part Number', 'MPN',
    'OEM Part Number', 'SKU', 'Product Name', 'Brand', 'Fitment',
    'Product Type', 'Type', 'Mileage', 'VIN', 'Vehicle Identification Number',
    'Quantity', 'Warranty', 'Stock Number', 'Inventory ID', 'Country',
    'Placement', 'Feature', 'Material', 'Number of', 'Length', 'Diameter', 'Width', 'Depth', 'Count',
    'Layer', 'Gear', 'Modular', 'Max', 'Number', 'Product'
]

def get_column_assignments(df, words):
    # Create a list to hold the mapping information
    mapping_info = []

    for col in df.columns:
        # Find the best match for the column name from the list of target words
        best_match, score = process.extractOne(col, words)
        # Append the column name, best match, and score to the list
        mapping_info.append({'Target Word': best_match, 'Original Column': col, 'Match Score': score})

    # Create a DataFrame from the mapping information
    mapping_df = pd.DataFrame(mapping_info)

    # Sort the DataFrame by match score in descending order
    mapping_df = mapping_df.sort_values(by='Match Score', ascending=False)

    return mapping_df

# Get the column assignments
mapping_df = get_column_assignments(df, words)

# Create a PrettyPrinter instance
pp = pprint.PrettyPrinter(compact=True)

# List of target words to display
target_words_to_display = [
    'Year', 'Make', 'Model', 'Manufacturer Part Number', 'MPN',
    'OEM Part Number', 'SKU', 'Product Name', 'Brand', 'Fitment',
    'Product Type', 'VIN', 'Vehicle Identification Number',
    'Stock Number', 'Inventory ID'
]

# Filter the mapping_df to include only the target words specified
filtered_mapping_df = mapping_df[mapping_df['Target Word'].isin(target_words_to_display)]

# Display the filtered mapping DataFrame
pp.pprint(filtered_mapping_df)

                        Target Word                           Original Column  Match Score
1578                           Year                                      year          100
27                             Make                                      Make          100
29                            Model                                     Model          100
32                              VIN                                     VIN #          100
33                             Year                                      Year          100
1577                           Make                                      make          100
38                     Product Name                              Product Name          100
129                 OEM Part Number                           OEM Part Number          100
25                     Inventory ID                              Inventory ID          100
46                              SKU                                       SKU          100

In [13]:
import pandas as pd
from fuzzywuzzy import process

# Function to get column assignments based on fuzzy matching
def get_column_assignments(df, words):
    mapping_info = []

    for col in df.columns:
        if col in ['RECORD_ID', 'ITEM_TAGS']:
            continue

        best_match, score = process.extractOne(col, words)
        mapping_info.append({'Target Word': best_match, 'Original Column': col, 'Match Score': score})

    mapping_df = pd.DataFrame(mapping_info)
    mapping_df = mapping_df[mapping_df['Match Score'] > 80]

    return mapping_df

# Function to clean and merge columns
def clean_and_merge_columns(df, mapping_df):
    # Ensure RECORD_ID is in the final DataFrame
    if 'RECORD_ID' in df.columns:
        final_columns = ['RECORD_ID']
    else:
        final_columns = []

    # Step 1: Remove any column in df with a column name not contained in 'Original Column' of mapping_df
    columns_to_keep = mapping_df['Original Column'].tolist()
    columns_to_keep.extend(final_columns)
    df = df[columns_to_keep]

    # Step 2: Combine values of the columns in 'Original Column' into their best match from 'Target Word'
    combined_data = {target_word: [] for target_word in mapping_df['Target Word'].unique()}
    for target_word in combined_data.keys():
        original_columns = mapping_df[mapping_df['Target Word'] == target_word]['Original Column']
        combined_data[target_word] = df[original_columns].apply(lambda row: [x for x in row if pd.notna(x)], axis=1).tolist()

    # Create a new DataFrame with the combined columns
    combined_df = pd.DataFrame(combined_data)

    # Step 3: Merge columns specified in merge_map
    merge_map = {
        'Manufacturer Part Number Clean': ['MPN', 'Manufacturer Part Number'],
        'Vehicle Identification Number Clean': ['VIN', 'Vehicle Identification Number'],
        'SKU Clean': ['Stock Number', 'Inventory ID', 'SKU']
    }

    for new_col, cols_to_merge in merge_map.items():
        combined_df[new_col] = combined_df[cols_to_merge].apply(lambda row: [x for sublist in row for x in sublist], axis=1)

    # Step 4: Remove 'Does Not Apply' values
    for col in combined_df.columns:
        combined_df[col] = combined_df[col].apply(lambda x: [item for item in x if item != 'Does Not Apply'])

    # Step 5: Drop unnecessary columns
    columns_to_drop = ['Country', 'Placement', 'Feature', 'Material', 'Quantity', 'Warranty', 'Number of', 'Length',
                       'Diameter', 'Width', 'Depth', 'Count','Layer', 'Gear', 'Modular', 'Max', 'Number', 'Product', 'Mileage']
    combined_df.drop(columns=[col for col in columns_to_drop if col in combined_df.columns], inplace=True)

    # Drop original columns after merging
    for cols_to_merge in merge_map.values():
        combined_df.drop(columns=cols_to_merge, inplace=True, errors='ignore')

    # Rename cleaned columns back to their original names
    rename_map = {
        'Manufacturer Part Number Clean': 'Manufacturer Part Number',
        'Vehicle Identification Number Clean': 'Vehicle Identification Number',
        'SKU Clean': 'SKU'
    }
    combined_df.rename(columns=rename_map, inplace=True)

    # Add RECORD_ID back to the combined DataFrame
    if 'RECORD_ID' in df.columns:
        combined_df['RECORD_ID'] = df['RECORD_ID']

    return combined_df

    
words = [
    'Year', 'Make', 'Model', 'Manufacturer Part Number', 'MPN',
    'OEM Part Number', 'SKU', 'Product Name', 'Brand', 'Fitment',
    'Product Type', 'Type', 'Mileage', 'VIN', 'Vehicle Identification Number',
    'Quantity', 'Warranty', 'Stock Number', 'Inventory ID', 'Country',
    'Placement', 'Feature', 'Material', 'Number of', 'Length', 'Diameter', 'Width', 'Depth', 'Count',
    'Layer', 'Gear', 'Modular', 'Max', 'Number', 'Product'
]

# Get the column assignments
mapping_df = get_column_assignments(df, words)

# Clean and merge columns
cleaned_df = clean_and_merge_columns(df, mapping_df)

final_df = cleaned_df.copy()

In [14]:
# Print the cleaned DataFrame (optional)
print(final_df.head(200))

                                         Brand                      Make                                                                                                                                                                                                       Model                                                                 Year                                                          Fitment                                                                                                                      Type                                                      OEM Part Number                                                                   Product Name Product Type                                                      Manufacturer Part Number Vehicle Identification Number                                             SKU  RECORD_ID
0                                      [Dayco]                   [Dodge]                                                                   

## Code below to enhance the years column. 
Implement algorithms to append "20" for cases where the year stated is only two digits. 

Observations: 
Looks like the year column is a list but isn't treating each year as a element. Instead it's a combination of words (typically) as one element.

In [15]:
print(final_df['Year'])

0                                                                    [1967]
1                                                                        []
2                                                                    [2018]
3                                                               [1986 1983]
4                                 [1999 2005 1998 2000 2001 2002 2003 2004]
5                                                     [1968 1969 1970 1971]
6                                                                        []
7                                                                        []
8                                                                 [1957 57]
9                                                                        []
10                                                                      [0]
11                                                                       []
12                                                                       []
13       [19

In [16]:
# Convert the 'Year' column to string
final_df['Year'] = final_df['Year'].astype(str)
# Remove Special Characters from each value in Year column
def remove_special_characters(year_str):
    return re.sub(r'[^0-9 ]', '', year_str)

# Apply the function to the 'Year' column
final_df['Year'] = final_df['Year'].apply(remove_special_characters)

In [17]:
# Replace all spaces with commas in the 'Year' column and then convert back to list
def process_year_column(year_str):
    # Replace spaces with commas
    comma_separated_str = year_str.replace(' ', ',')
    # Convert to list of integers
    year_list = [int(year) for year in comma_separated_str.split(',') if year]
    # Adjust two-digit and one-digit years to four digits
    corrected_years = []
    for year in year_list:
        if year < 100:
            if year < 25:
                corrected_years.append(2000 + year)
            else:
                corrected_years.append(1900 + year)
        else:
            corrected_years.append(year)
    return corrected_years

# Apply the function to the 'Year' column
final_df['Year'] = final_df['Year'].apply(process_year_column)

In [18]:
print(final_df.head(200))

                                         Brand                      Make                                                                                                                                                                                                       Model                                                                                              Year                                                          Fitment                                                                                                                      Type                                                      OEM Part Number                                                                   Product Name Product Type                                                      Manufacturer Part Number Vehicle Identification Number                                             SKU  RECORD_ID
0                                      [Dayco]                   [Dodge]                                      

## Item Title and Description Imports
Use Item Title to populate missing information from tags

**Use the code block below if you are on Google Colab**

In [19]:
# ## Use this block if you are on Google Colab
# index_max = 500
# items_df = pd.read_csv(items)
# print(items_df.shape)
# items_df = items_df[:index_max]
# print(items_df.shape)
# items_df.head()

#### Converting base64 to UTF-8

In [20]:
# Function to decode base64 encoded strings
def decode_base64_string(encoded_str):
    try:
        # Decode the base64 string and then decode the bytes to a utf-8 string
        return base64.b64decode(encoded_str).decode('utf-8')
    except Exception as e:
        return str(e)

# Apply the decode function to the ITEM_DESC column
desc_df['Decoded_DESC'] = desc_df['ITEM_DESC'].apply(decode_base64_string)

print("Decoded Description")

# Try to clean the HTML content in Decoded_DESC
def clean_html(html_content):
    if not isinstance(html_content, str):
        return ""
    soup = BeautifulSoup(html_content, 'html.parser')
    text = soup.get_text(separator=" ")
    text = re.sub(r'\s+', ' ', text).strip()
    return text

desc_df['Cleaned_DESC'] = desc_df['Decoded_DESC'].apply(clean_html)

print("Cleaned Description")

# Drop columns that are not needed
desc_df = desc_df.drop(columns=['ITEM_DESC'])

Decoded Description


/var/folders/m1/wdssqg4s5836yf46c6t8lxh00000gn/T/ipykernel_24396/841822250.py:18: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(html_content, 'html.parser')


Cleaned Description


## Join the Description Dataframe and the Items Dataframe together

In [21]:
# join df_desc and df_items on RECORD_ID
df = pd.merge(desc_df, items_df, on='RECORD_ID', how='outer')

# Drop the Decoded_desc column
df = df.drop(columns=['Decoded_DESC'])

In [22]:
# Check to make sure that all record ID's still are in the data
print(df['RECORD_ID'].head(20))

0      0
1      1
2      2
3      3
4      4
5      5
6      6
7      7
8      8
9      9
10    10
11    11
12    12
13    13
14    14
15    15
16    16
17    17
18    18
19    19
Name: RECORD_ID, dtype: int64


### Remove Special Characters

In [23]:
# Function to clean description while retaining hyphens
def clean_description(description):
    if isinstance(description, str):
        description = description.lower()  # Normalize text to lowercase
        description = re.sub(r'[^a-z0-9\s-]', '', description)  # Remove special characters and punctuation except hyphens
    return description

# Apply cleaning function
df['ITEM_TITLE'] = df['ITEM_TITLE'].apply(clean_description)
df['Cleaned_DESC'] = df['Cleaned_DESC'].apply(clean_description)

## Extract the Years from Description and Title

In [25]:
# Regular expression pattern to find years and ranges like "99-03", "99 - 03", or "2007-2015"
year_pattern = re.compile(r'\b(\d{2}\s*-\s*\d{2}|\d{4}\s*-\s*\d{4}|\d{4})\b')

# Function to expand ranges like "99-03", "99 - 03", or "2007-2015" into individual years and check the range
def expand_year_range(year_range):
    start, end = year_range.replace(' ', '').split('-')  # Remove spaces before splitting
    if len(start) == 2:  # Handle 2-digit years
        start = '19' + start if int(start) > 22 else '20' + start
    if len(end) == 2:  # Handle 2-digit years
        end = '19' + end if int(end) > 22 else '20' + end
    start, end = int(start), int(end)
    
    # Check if the years are within the acceptable range
    if start < 1904:
        start = 1904
    if end > 2024:
        end = 2024
    
    return [str(year) for year in range(start, end + 1)]

# Function to extract years from a single column with range expansion, ignoring "copyright"
def extract_years_from_column(text):
    years = year_pattern.findall(text)
    all_years = set()

    for year in years:
        if '-' in year:  # Expand ranges like "99-03" or "2007-2015"
            if f"copyright {year}" not in text:
                all_years.update(expand_year_range(year))
        else:
            year_int = int(year)
            if 1904 <= year_int <= 2024 and f"copyright {year}" not in text:
                all_years.add(year)

    sorted_years = sorted(all_years)
    return ', '.join(sorted_years) if sorted_years else None

# Extract years into separate columns
df['Extracted_Years_FROM_TITLE'] = df['ITEM_TITLE'].astype(str).apply(extract_years_from_column)

In [26]:
df.drop(columns=['Cleaned_DESC'], inplace=True)

In [27]:
print(df.head(10))

   RECORD_ID  CATEGORY                                                                       ITEM_TITLE                      Extracted_Years_FROM_TITLE
0          0       1.0     dayco upper radiator coolant hose for 1967 dodge w100 series 63l v8 belts ky                                            1967
1          1       4.0          2007 corolla front driver left cv axle shaft oem 91k miles lkq336959456                                            2007
2          2       0.0                                      alternator 4 cylinder fits 18 altima 187356                                            None
3          3       0.0           for 1983 ford mustang starter motor relay connector smp 84469jxjr 1986                                      1983, 1986
4          4       2.0   for 1998-2005 mercedes clk320 crankcase breather hose febi 81245rkmk 1999 2000  1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005
5          5       2.0                 for 1968-1971 mercedes 280s camshaft gear febi 37

# Merge Tags with Extracted Years from TITLE
Where we have NA we will input the years from title

In [28]:
data_extracted = df.copy()

# Merge the dataframes on record_id
merged_df = final_df.merge(df, on='RECORD_ID', how='left')

merged_df.head()

Brand      Make          Model                                              Year               Fitment                     Type OEM Part Number                                               Product Name Product Type                  Manufacturer Part Number Vehicle Identification Number               SKU  RECORD_ID  CATEGORY                                                                      ITEM_TITLE                      Extracted_Years_FROM_TITLE
0                    [Dayco]   [Dodge]  [W100 Series]                                            [1967]  [Direct Replacement]  [Radiator Coolant Hose]              []                                                         []           []  [SX-6425 1967 Belts Cooling Hoses Pipes]                            []                []          0       1.0    dayco upper radiator coolant hose for 1967 dodge w100 series 63l v8 belts ky                                            1967
1                   [Toyota]        []             []                                                []                    []                       []              []                                                         []           []                    [Corolla~336959456LKQ]           [JTDBR32E770118632]                []          1       4.0         2007 corolla front driver left cv axle shaft oem 91k miles lkq336959456                                            2007
2                   [NISSAN]  [NISSAN]       [ALTIMA]                                            [2018]                    []                       []              []                                                         []           []                                        []           [1N4AL3AP8JC163431]  [211207, 187356]          2       0.0                                     alternator 4 cylinder fits 18 altima 187356                                            None
3  [Standard Motor Products]        []             []                                      [1986, 1983]                    []                       []     [84469JXJR]                            [Starter Motor Relay Connector]           []                               [84469JXJR]                            []   [400:84469JXJR]          3       0.0          for 1983 ford mustang starter motor relay connector smp 84469jxjr 1986                                      1983, 1986
4                     [Febi]        []             []  [1999, 2005, 1998, 2000, 2001, 2002, 2003, 2004]                    []                       []     [81245RKMK]  [Crankcase Breather Hose, Engine Crankcase Breather Hose]           []                               [81245RKMK]                            []   [400:81245RKMK]          4       2.0  for 1998-2005 mercedes clk320 crankcase breather hose febi 81245rkmk 1999 2000  1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005

In [30]:
# Change all values in 'Exetracted_Years_FROM_TITLE' and 'Extracted_Years_FROM_DESC' to list
merged_df['Extracted_Years_FROM_TITLE'] = merged_df['Extracted_Years_FROM_TITLE'].apply(lambda x: x.split(', ') if isinstance(x, str) else [])

In [31]:
merged_df['Year_New'] = merged_df['Year']
# Iterate through each "Year" and "Extracted_Years_FROM_TITLE" 
for index, row in merged_df.iterrows():
    # Get the "Year" and "Extracted_Years_FROM_TITLE" values
    year = row['Year']
    extracted_years = row['Extracted_Years_FROM_TITLE']
    
    # Check if extracted_years is a list
    if isinstance(extracted_years, list):
        # If year is empty, populate it with extracted_years
        if not year:
            year = extracted_years
        else:
            # Iterate through each year in the extracted_years list
            for y in extracted_years:
                # Check if the year is not in the year list
                if y not in year:
                    # Append the year to the year list
                    year.append(y)
    
    # Update the "Year_New" column with the updated list
    merged_df.at[index, 'Year_New'] = year

In [32]:
# Count NA values in 'Year_New' column
empty_list_count_yr_new = merged_df['Year_New'].apply(lambda x: len(x) == 0).sum()
empty_list_count_yr = merged_df['Year'].apply(lambda x: len(x) == 0).sum()

print(f"Populated {empty_list_count_yr - empty_list_count_yr_new} empty lists in 'Year_New' column with values from 'Extracted_Years_FROM_TITLE' column")

Populated 1515 empty lists in 'Year_New' column with values from 'Extracted_Years_FROM_TITLE' column


## We want to fix a few years in this. Some of the years look like "20222023". Implement logic where if a year is 8 characters, then put a comma after the 4th

In [33]:
# Loop through each row and element in 'Year_New' column and change 8 digit years to two 4 digit years separated by a comma ("20202019") to ("2020, 2019")
for index, row in merged_df.iterrows():
    # Get the 'Year_New' value
    year = row['Year_New']
    # Check if year is a list
    if isinstance(year, list):
        # Iterate through each element in the list
        for i in range(len(year)):
            # Convert the element to a string
            year[i] = str(year[i])
            # Check if the element is a string and has a length of 8
            if isinstance(year[i], str) and len(year[i]) == 8:
                # Split the 8 digit year into two 4 digit years
                year[i] = year[i][:4] + ', ' + year[i][4:]
        # Update the 'Year_New' column with the updated list
        merged_df.at[index, 'Year_New'] = year

In [34]:
# Fix the "20122013201420152016" in the 'Year_New' column
for index, row in merged_df.iterrows():
    # Get the 'Year_New' value
    year = row['Year_New']
    # Check if year is a list
    if isinstance(year, list):
        # Iterate through each element in the list
        for i in range(len(year)):
            # Convert the element to a string
            year[i] = str(year[i])
            # Check if the element is a string and has a length of 20
            if isinstance(year[i], str) and len(year[i]) == 20:
                # Split the 20 digit year into five 4 digit years
                year[i] = year[i][:4] + ', ' + year[i][4:8] + ', ' + year[i][8:12] + ', ' + year[i][12:16] + ', ' + year[i][16:]
        # Update the 'Year_New' column with the updated list
        merged_df.at[index, 'Year_New'] = year

In [35]:
# Convert the 'Year_New' column to string
merged_df['Year_New'] = merged_df['Year_New'].apply(lambda x: ', '.join(x) if isinstance(x, list) else x)

# Now Convert back to a list
merged_df['Year_New'] = merged_df['Year_New'].apply(lambda x: x.split(', ') if isinstance(x, str) else [])

In [36]:
more_than_4 = False
# Make sure each element in 'Year_New' is of length 4
for index, row in merged_df.iterrows():
    # Get the 'Year_New' value
    year = row['Year_New']
    # Check if year is a list
    if isinstance(year, list):
        # Iterate through each element in the list
        for i in range(len(year)):
            # Convert the element to a string
            year[i] = str(year[i])
            # Check if the element is a string and has a length greater than 4
            if isinstance(year[i], str) and len(year[i]) > 4:
                more_than_4 = True

                # Print the element
                print(year[i])

# Print the result
if more_than_4 == True:
    print("Warning: There  are more than 4 digit years in the 'Year_New' column")

In [38]:
final_df = merged_df.copy()
# Replace the 'Year' column with the 'Year_New' column
final_df['Year'] = final_df['Year_New']
# Drop the 'Year_New' and 'Extracted_Years_FROM_TITLE' and "Extracted_Years_FROM_DESC" column
final_df.drop(columns=['Year_New', 'Extracted_Years_FROM_TITLE'], inplace=True)

# Move Record_ID to the first column
cols = final_df.columns.tolist()
cols = ['RECORD_ID'] + [col for col in cols if col != 'RECORD_ID']
final_df = final_df[cols]

## Populate Make

In [39]:
# Check if "ITEM_TITLE" is a list
year_column_has_lists = final_df['ITEM_TITLE'].apply(lambda x: isinstance(x, list)).all()
print(f"'ITEM_TITLE' column contains only lists: {year_column_has_lists}")

'ITEM_TITLE' column contains only lists: False


In [40]:
# Get a list of car makes and models
ebay_folder = "eBay_ML_Challenge_2024_part1"

cars_full_file_path = os.path.join(cwd, ebay_folder, "ftmnt_train.csv.gz")
cars = pd.read_csv(cars_full_file_path, compression='gzip', nrows=10000)

unique_makes = cars['FTMNT_MAKE'].unique().tolist()
unique_models = cars['FTMNT_MODEL'].unique().tolist()
# unique_items = items['ITEM_TITLE'].unique().tolist()

# Check if 'case' is in unique_makes
print('CASE' in [make.upper() for make in unique_makes])

# List of common car makes https://gist.github.com/pcgeek86/78f4cad29dd16961ceeeee654127a0db

def find_make_or_model(description, column_name):
    if column_name == 'make':
        pattern = re.compile(r'\b(' + '|'.join(re.escape(make) for make in unique_makes) + r')\b', re.IGNORECASE)
    elif column_name == 'model':
        pattern = re.compile(r'\b(' + '|'.join(re.escape(model) for model in unique_models) + r')\b', re.IGNORECASE)
    else:
        return None
    
    if isinstance(description, str):
        match = pattern.search(description)
        return match.group(1) if match else None
    else:
        return None

# Ensure all values in the 'ITEM_TITLE' column are strings
final_df['ITEM_TITLE'] = final_df['ITEM_TITLE'].astype(str)

# Apply the function to create new columns for car make and model
final_df['ext_make'] = final_df['ITEM_TITLE'].apply(lambda x: find_make_or_model(x, 'make'))
final_df['ext_model'] = final_df['ITEM_TITLE'].apply(lambda x: find_make_or_model(x, 'model'))

# Display the DataFrame with new columns
print(final_df[['ITEM_TITLE', 'ext_make', 'ext_model']].head())

True
                                                                       ITEM_TITLE ext_make    ext_model
0    dayco upper radiator coolant hose for 1967 dodge w100 series 63l v8 belts ky    dodge  w100 series
1         2007 corolla front driver left cv axle shaft oem 91k miles lkq336959456     None      corolla
2                                     alternator 4 cylinder fits 18 altima 187356     None       altima
3          for 1983 ford mustang starter motor relay connector smp 84469jxjr 1986     ford      mustang
4  for 1998-2005 mercedes clk320 crankcase breather hose febi 81245rkmk 1999 2000     None       clk320


In [41]:
# Switch Make and Model to String
final_df['Make'] = final_df['Make'].apply(lambda x: x[0] if x else None)
final_df['Model'] = final_df['Model'].apply(lambda x: x[0] if x else None)

print(final_df[['Make','Model']].head())

     Make        Model
0   Dodge  W100 Series
1    None         None
2  NISSAN       ALTIMA
3    None         None
4    None         None


In [42]:
# Count the number of missing values in 'Make' and 'Model'
missing_make_count = final_df['Make'].isnull().sum()
missing_model_count = final_df['Model'].isnull().sum()

print(f"Missing values in 'Make' column: {missing_make_count}")
print(f"Missing values in 'Model' column: {missing_model_count}")

# Now if Make is empty, we can fill it with the extracted make
final_df['Make'] = final_df['Make'].combine_first(final_df['ext_make'])
final_df['Model'] = final_df['Model'].combine_first(final_df['ext_model'])


# Change all values in 'Make' and 'Model' to uppercase
final_df['Make'] = final_df['Make'].str.upper()
final_df['Model'] = final_df['Model'].str.upper()

# Count the number of missing values in 'Make' and 'Model'
missing_make_count = final_df['Make'].isnull().sum()
missing_model_count = final_df['Model'].isnull().sum()

# Print the number of missing values in 'Make' and 'Model'
print(f"Missing values in 'Make' column: {missing_make_count}")
print(f"Missing values in 'Model' column: {missing_model_count}")

print(final_df[['Make','Model', 'ext_make', 'ext_model']].head(200))


Missing values in 'Make' column: 3754
Missing values in 'Model' column: 3780
Missing values in 'Make' column: 1275
Missing values in 'Model' column: 1276
                       Make                                                            Model       ext_make         ext_model
0                     DODGE                                                      W100 SERIES          dodge       w100 series
1                      None                                                          COROLLA           None           corolla
2                    NISSAN                                                           ALTIMA           None            altima
3                      FORD                                                          MUSTANG           ford           mustang
4                      None                                                           CLK320           None            clk320
5                      None                                                             28

In [43]:
# Drop ext_make and ext_model columns
final_df.drop(columns=['ext_make', 'ext_model'], inplace=True)

# Print the first few rows of the final DataFrame
print(final_df.head(500))

     RECORD_ID                                               Brand                                       Make                                                              Model                                                                                                                                                                                                          Year                                                                                                                                                      Fitment                                                                                                                      Type                                                      OEM Part Number                                                                   Product Name           Product Type                                                      Manufacturer Part Number Vehicle Identification Number                                              SKU  \
0      

In [44]:
# It looks like Type and Product Type should be the same, so we can merge them
final_df['Type'] = final_df['Type'].combine_first(final_df['Product Type']) # Put the values of 'Product Type' into 'Type' if 'Type' is missing
final_df.drop(columns=['Product Type'], inplace=True) # Drop the 'Product Type' column

In [45]:
# Print the New Type column
print(final_df['Type'].head(25))

0                             [Radiator Coolant Hose]
1                                                  []
2                                                  []
3                                                  []
4                                                  []
5                                                  []
6                                                  []
7     [Automatic Transmission Extension Housing Seal]
8                                                  []
9                                 [Engine Oil Filter]
10                                                 []
11                                                 []
12                                       [Spark Plug]
13                                                 []
14                        [Direct Ignition Coil Boot]
15                                       [Alternator]
16                                 [Engine Mount Kit]
17                                                 []
18                          

## Populate Part Types with Extraction from Title

In [46]:
part_types = [
    'air filter', 'alternator', 'battery', 'brake caliper', 'brake disc',
    'brake drum', 'brake pad', 'brake rotor', 'bumper', 'camshaft', 'carburetor',
    'catalytic converter', 'clutch', 'control arm', 'coolant reservoir', 'crankshaft',
    'cv joint', 'differential', 'distributor', 'door handle', 'drive belt', 'drive shaft',
    'engine block', 'engine mount', 'exhaust manifold', 'fan belt', 'fuel filter',
    'fuel injector', 'fuel pump', 'fuel tank', 'fuse box', 'gasket', 'grille',
    'head gasket', 'headlight', 'heater core', 'horn', 'ignition coil', 'ignition switch',
    'intake manifold', 'intercooler', 'instrument cluster', 'leaf spring', 'muffler',
    'oil filter', 'oil pump', 'oil pan', 'oxygen sensor', 'piston', 'power steering pump',
    'radiator', 'radiator hose', 'relay', 'rocker arm', 'seat belt', 'shock absorber',
    'spark plug', 'speedometer', 'starter motor', 'steering column', 'steering gear',
    'strut', 'suspension arm', 'tail light', 'thermostat', 'throttle body', 'timing belt',
    'timing chain', 'timing cover', 'torque converter', 'transmission', 'turbocharger',
    'valve cover', 'water pump', 'wheel bearing', 'wheel hub', 'windshield', 'windshield wiper',
    'wiper blade', 'wiper motor', 'air conditioning compressor', 'air conditioning condenser',
    'air conditioning evaporator', 'air conditioning expansion valve', 'air conditioning hose',
    'air conditioning receiver drier', 'blower motor', 'blower resistor', 'clutch master cylinder',
    'clutch slave cylinder', 'control module', 'cruise control module', 'dashboard', 'door',
    'door panel', 'drive belt tensioner', 'engine control unit (ECU)', 'engine oil cooler',
    'evaporative emissions canister', 'fuel rail', 'glove box', 'headlamp assembly', 'hood',
    'idle air control valve', 'intake air temperature sensor', 'intake valve', 'knock sensor',
    'leaf spring shackle', 'liftgate', 'lower control arm', 'mass air flow sensor', 'mirror',
    'motor mount', 'oil cooler', 'oil dipstick', 'oil filler cap', 'oil pressure sensor',
    'parking brake cable', 'parking brake lever', 'pedal', 'power seat motor', 'pressure plate',
    'rear axle', 'rear view mirror', 'roof rack', 'seat', 'shock mount', 'side marker light',
    'spare tire', 'spark plug wire', 'spoiler', 'stabilizer bar', 'steering knuckle',
    'steering wheel', 'sunroof motor', 'sway bar', 'sway bar link', 'temperature sensor',
    'throttle position sensor', 'tire', 'trailing arm', 'trunk lid', 'turn signal switch',
    'upper control arm', 'vacuum pump', 'valve', 'valve spring', 'valve stem seal',
    'water pump gasket', 'window motor', 'window regulator', 'windshield washer pump',
    'windshield washer reservoir', 'windshield washer nozzle', 'windshield washer hose',
    'airbag', 'antenna', 'ashtray', 'belt tensioner', 'brake booster', 'brake line',
    'brake master cylinder', 'brake pedal', 'brake proportioning valve', 'cabin air filter',
    'camshaft position sensor', 'clutch cable', 'coolant temperature sensor', 'crankshaft position sensor',
    'cylinder head', 'dash cover', 'differential cover', 'door latch', 'door lock actuator',
    'door mirror', 'drive shaft bearing', 'emergency brake', 'engine cover', 'exhaust pipe',
    'floor mat', 'fog light', 'fuel cap', 'fuel door', 'fuel line', 'gas cap', 'glove box latch',
    'grill guard', 'heater control valve', 'hood latch', 'hood release cable', 'idle control valve',
    'ignition control module', 'ignition lock cylinder', 'ignition switch', 'intercooler hose',
    'interior door handle', 'jack handle', 'kick panel', 'knuckle', 'leaf spring bushing',
    'lift support', 'license plate light', 'lock cylinder', 'map light', 'mass air flow meter',
    'moonroof', 'oil filter adapter', 'oil filter housing', 'oil level sensor', 'parking light',
    'pillar trim', 'pitman arm', 'power antenna', 'power door lock', 'power mirror', 'power seat switch',
    'power steering hose', 'quarter panel', 'radiator cap', 'radiator fan', 'rear differential',
    'rearview camera', 'rocker panel', 'running board', 'seat cushion', 'seat track', 'shock boot',
    'side mirror', 'skid plate', 'sliding door', 'smog pump', 'spare wheel', 'spark plug boot',
    'splash guard', 'steering shaft', 'sunroof glass', 'sunvisor', 'tachometer', 'tailgate',
    'tailgate handle', 'third brake light', 'tie rod', 'tie rod end', 'timing belt cover',
    'torque arm', 'torsion bar', 'tow hook', 'trailer hitch', 'transfer case motor', 'turn signal light',
    'vacuum hose', 'valve cover gasket', 'valve lifter', 'vanity mirror', 'vent window', 'voltage regulator',
    'wheel', 'window crank', 'window glass', 'window seal', 'wiper arm', 'wiper blade refills',
    'wiper linkage', 'air intake', 'air suspension compressor', 'armrest', 'back glass',
    'battery cable', 'battery tray', 'bed liner', 'bicycle rack', 'blower fan', 'body control module',
    'boost control solenoid', 'brake backing plate', 'brake dust shield', 'brake hose', 'bushing',
    'cam bearing', 'camshaft sensor', 'canister purge valve', 'cargo cover', 'catalytic converter shield',
    'center console', 'charge pipe', 'coil spring', 'coolant hose', 'cooling fan', 'crossmember',
    'cv boot', 'cv shaft', 'dashboard light', 'deck lid', 'door seal', 'drive shaft yoke', 'driveshaft',
    'engine oil filter', 'exhaust hanger', 'exhaust system', 'fan clutch', 'fan shroud', 'fender',
    'fire extinguisher', 'floor pan', 'flywheel', 'fog lamp', 'front bumper', 'front differential',
    'fuel gauge', 'fuel pump relay', 'fuel rail pressure sensor', 'fuel tank strap', 'glove compartment',
    'headlight bulb', 'headlight switch', 'hood hinge', 'horn button', 'hydraulic hose', 'idler arm',
    'ignition relay', 'intake hose', 'intake pipe', 'intercooler pipe', 'interior light', 'jack stand',
    'keyless entry remote', 'kick plate', 'lamp assembly', 'leaf spring hanger', 'license plate bracket',
    'lift kit', 'lug nut', 'oil cooler line', 'oil pressure switch', 'overhead console', 'parking brake handle',
    'parking sensor', 'pedal pad', 'pillar panel', 'pitman shaft', 'power brake booster', 'power door lock actuator',
    'power seat frame', 'power steering control module', 'quarter window', 'radiator hose clamp',
    'radiator support', 'rear bumper', 'rear differential cover', 'rocker panel molding', 'roof panel',
    'roof spoiler', 'seat base', 'seat cover', 'shock absorber bushing', 'side airbag', 'side view mirror',
    'sliding window', 'smoke detector', 'spark plug gap tool', 'speed sensor', 'spindle nut', 'spoiler lip',
    'stabilizer link', 'stator', 'steering box', 'steering gear box', 'steering rack', 'strut assembly',
    'subframe', 'sunroof shade', 'tachometer sensor', 'tail panel', 'tailgate cap', 'tailgate light',
    'tensioner pulley', 'thermostat housing', 'throttle cable', 'throttle linkage', 'throttle position sensor connector',
    'timing gear', 'timing sprocket', 'tire pressure sensor', 'tow bar', 'trailer brake controller', 'trailer hitch ball',
    'transfer case shifter', 'transmission cooler', 'turn signal flasher', 'valve guide', 'valve seat',
    'valve stem', 'valve train', 'vanity light', 'vent shade', 'voltage regulator brush', 'wheel cover',
    'wheel lock', 'wheel spacer', 'wind deflector', 'window guide', 'window latch', 'window molding',
    'windshield molding', 'wiper blade arm', 'wiper motor transmission', 'wood grain dash kit'
]


def extract_part_type(description):
    if isinstance(description, str):
        part_counts = Counter()
        for part in part_types:
            matches = re.findall(r'\b' + re.escape(part) + r'\b', description)
            part_counts[part] += len(matches)
        if part_counts:
            most_common_part = part_counts.most_common(1)[0][0]
            return most_common_part
    return 'unknown'

items_df['Part_Type'] = items_df['ITEM_TITLE'].apply(extract_part_type)

items_df.head()

RECORD_ID  CATEGORY                                                                      ITEM_TITLE   Part_Type
0          0         1   Dayco Upper Radiator Coolant Hose for 1967 Dodge W100 Series 6.3L V8 Belts ky  air filter
1          1         4      2007 Corolla Front Driver Left CV Axle Shaft OEM 91K Miles (LKQ~336959456)  air filter
2          2         0                                     Alternator 4 Cylinder Fits 18 ALTIMA 187356  air filter
3          3         0          For 1983 Ford Mustang Starter Motor Relay Connector SMP 84469JXJR 1986  air filter
4          4         2  For 1998-2005 Mercedes CLK320 Crankcase Breather Hose Febi 81245RKMK 1999 2000  air filter

In [47]:
# Filter items_df for "RECORD_ID" and "Part_Type" columns
items_df = items_df[['RECORD_ID', 'Part_Type']]
# Merge the dataframes on record_id
merged_df = final_df.merge(items_df, on='RECORD_ID', how='left')

# Populate the "Type" column with the "Part_Type" column
merged_df['Type'] = merged_df['Type'].combine_first(merged_df['Part_Type'])

# Drop the "Part_Type" column
merged_df.drop(columns=['Part_Type'], inplace=True)

# Print the first few rows of the final DataFrame
print(merged_df.head(500))

     RECORD_ID                                               Brand                                       Make                                                              Model                                                                                                                                                                                                          Year                                                                                                                                                      Fitment                                                                                                                      Type                                                      OEM Part Number                                                                   Product Name                                                      Manufacturer Part Number Vehicle Identification Number                                              SKU  CATEGORY  \
0            0      

## Run the code below to regenerate the final_df dataframe

In [43]:
# Save resulting DataFrame to a 'final_df'  
final_df = merged_df.copy()

# Save the final DataFrame to a CSV file
final_df.to_csv('final_df.csv', index=False)

## Start manipulation to One-Hot Encode
Used to prepare data for ML Models

Note: Rerun the above cell to get final_df back because we are overwriting final_df in the next codes

In [44]:
# Import the fitment data
fitment_full_file_path = os.path.join(cwd, ebay_folder, "ftmnt_train.csv.gz")
fitment_df = pd.read_csv(fitment_full_file_path, compression='gzip', nrows=10000)

# We only want the FTMNT_MAKE and FTMNT_MODEL columns
fitment_df = fitment_df[['FTMNT_MAKE', 'FTMNT_MODEL']]

# Summary of the fitment data
fitment_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   FTMNT_MAKE   10000 non-null  object
 1   FTMNT_MODEL  10000 non-null  object
dtypes: object(2)
memory usage: 156.4+ KB


In [45]:
# Prepare the 'Type' Column for one-hot encoding
def clean_value(value):
    if isinstance(value, list):
        return [item.replace(';', '').replace('+', ',').replace('/', ',').replace('and', ',').replace(' & ', ', ') for item in value]
    elif isinstance(value, str):
        return value.replace(';', '').replace('+', ',').replace('/', ',').replace('and', ',').replace(' & ', ', ')
    else:
        return value

# Apply the function to the "Type" column
final_df['Type'] = final_df['Type'].apply(clean_value)

def replace_comma_space(value):
    if isinstance(value, list):
        return [item.replace(' , ', ',') for item in value]
    elif isinstance(value, str):
        return value.replace(' , ', ',')
    else:
        return value
    
final_df['Type'] = final_df['Type'].apply(replace_comma_space)

# Upper case the values in the 'Type' column
final_df['Type'] = final_df['Type'].apply(lambda x: [item.upper() for item in x] if isinstance(x, list) else x.upper())

In [46]:
# # Convert each list into a string seperated by commas
final_df['Type'] = final_df['Type'].apply(lambda x: ','.join(x) if isinstance(x, list) else x)

# Replace all ", " with ","
final_df['Type'] = final_df['Type'].str.replace(', ', ',')

# Now convert back to lists of strings separated by commas
final_df['Type'] = final_df['Type'].apply(lambda x: x.split(',') if isinstance(x, str) else x)

In [47]:
# One-hot encode the 'Type' column
# Type is a series of lists so we need to import MultiLabelBinarizer
from sklearn.preprocessing import MultiLabelBinarizer

# Create an instance of MultiLabelBinarizer
mlb = MultiLabelBinarizer()

res = pd.DataFrame(mlb.fit_transform(final_df['Type']), columns=mlb.classes_, index=final_df.index)

# Prefix the one-hot encoded columns and replace spaces with underscores
res.columns = 'TYPE_' + res.columns.str.replace(' ', '_')

# Concatenate the one-hot encoded columns to the final DataFrame
final_one_hot_df = pd.concat([final_df['RECORD_ID'], res], axis=1)


In [49]:
# Remove the "#" and the "/" column
final_one_hot_df.drop(columns=['TYPE_#'], inplace=True)

In [51]:
# Print Column Names 
print(final_one_hot_df.columns)

Index(['RECORD_ID', 'TYPE_', 'TYPE_12"_FAN_KIT', 'TYPE_12*_SEAL_VALVE_STEM', 'TYPE_2*12''FAN', 'TYPE_3-PRONG_THREE_CAVITY_MALE_TERMINAL_1_FEMALE_CONNECTOR', 'TYPE_3-WAY', 'TYPE_3.2L', 'TYPE_3.5L', 'TYPE_4_POLE',
       ...
       'TYPE_WATER_PUMPS', 'TYPE_WATER_TEMPERATURE_SENDER', 'TYPE_WATER_TEMPERATURE_SENSOR', 'TYPE_WHEEL_HUB_ASSEMBLY', 'TYPE_WHEEL_HUB_ASSEMBLY_KIT', 'TYPE_WIPER_MOTOR', 'TYPE_WIRE_HARNESS', 'TYPE_XTREME_ENERGY_HI-LIFT_CAMSHAFT', 'TYPE_YAW_RATE_SENSOR_CONNECTOR', 'TYPE_YES'], dtype='object', length=884)


In [52]:
# Remove "-" from the 'Make' and 'Model' columns
final_df['Make'] = final_df['Make'].str.replace(r'\s|-', '')
final_df['Model'] = final_df['Model'].str.replace(r'\s|-', '')

# Remove Spaces from the 'Make' and 'Model' columns
final_df['Make'] = final_df['Make'].str.replace(' ', '')
final_df['Model'] = final_df['Model'].str.replace(' ', '')

# Replace NA values with 'Other' in the 'Make' and 'Model' column
final_df['Make'] = final_df['Make'].fillna('Other')
final_df['Model'] = final_df['Model'].fillna('Other')

# Print the first few rows of make and model columns
print(final_df[['Make', 'Model']].head(2000))

                                                       Make                                                      Model
0                                                     DODGE                                                 W100SERIES
1                                                     Other                                                      Other
2                                                    NISSAN                                                     ALTIMA
3                                                      FORD                                                    MUSTANG
4                                                     Other                                                      Other
5                                                     Other                                                      Other
6                                                     Other                                                      Other
7                                               

In [53]:
# Convert the 'Make' and 'Model' columns to List separated by commas
final_df['Make'] = final_df['Make'].apply(lambda x: x.split(','))
final_df['Model'] = final_df['Model'].apply(lambda x: x.split(','))

In [54]:
# Create dummies
mlb = MultiLabelBinarizer()
res = pd.DataFrame(mlb.fit_transform(final_df['Make']), columns=mlb.classes_, index=final_df.index)

# Add prefix to the columns and replace spaces with underscores
res.columns = 'MAKE_' + res.columns.str.replace(' ', '_')

# Concatenate the one-hot encoded columns to the final DataFrame
final_one_hot_df = pd.concat([final_one_hot_df, res], axis=1)

# Create Dummies for Model
mlb = MultiLabelBinarizer()
res = pd.DataFrame(mlb.fit_transform(final_df['Model']), columns=mlb.classes_, index=final_df.index)

# Add prefix to the columns and replace spaces with underscores
res.columns = 'MODEL_' + res.columns.str.replace(' ', '_')

# Concatenate the one-hot encoded columns to the final DataFrame
final_one_hot_df = pd.concat([final_one_hot_df, res], axis=1)


In [55]:
print(final_one_hot_df.head(10))

   RECORD_ID  TYPE_  TYPE_12"_FAN_KIT  TYPE_12*_SEAL_VALVE_STEM  TYPE_2*12''FAN  TYPE_3-PRONG_THREE_CAVITY_MALE_TERMINAL_1_FEMALE_CONNECTOR  TYPE_3-WAY  TYPE_3.2L  TYPE_3.5L  TYPE_4_POLE  TYPE_4-PIN  TYPE_4-SPEED_AUTOMATIC_TRANSMISSION  TYPE_4WD  TYPE_4WD_SWITCH  TYPE_6-SPEED_MANUAL  TYPE_6-SPEED_NV5600_MANUAL_TRANSMISSION  TYPE_722  TYPE_74  TYPE_75W-90  TYPE_8691  TYPE_9  TYPE_90_DEGREE  TYPE_A  TYPE_AC_CONDENSER  TYPE_ACCESSORY_POWER_RELAY  TYPE_ACTUATOR  TYPE_ADAPTER  TYPE_AIR_COMPRESSOR_AC_BRACKET  TYPE_ALTERNATOR  TYPE_ALTERNATOR_BEARING  TYPE_ALTERNATOR_BRUSH_SET  TYPE_ALTERNATOR_CONNECTOR  TYPE_AMBIENT_AIR_TEMPERATURE_SENSOR_CONNECTOR  TYPE_ANTENNA  TYPE_ARD  TYPE_ARD_BLADE_FUSE  TYPE_ARD_FUSE  TYPE_ARD)  TYPE_AS_SHOWN_IN_THE_PICTURE  TYPE_AUTO  TYPE_AUTO_SHUT_DOWN_RELAY_CONNECTOR  TYPE_AUTO_TRANS_ACTUATOR_FEED_LIMIT_VALVE_PLUG_RETAINER  TYPE_AUTO_TRANS_DIPSTICK_TUBE  TYPE_AUTO_TRANS_DRAIN_PLUG  TYPE_AUTO_TRANS_OUTPUT_SHAFT_SPEED_SENSOR  TYPE_AUTO_TRANSMISSION_FILTER_KIT  \
0  

### The above code, we cleaned the MAKE, MODEL, and TYPE columns and then one-hot encoded. Now proceed with one-hot encoding and the "brand" feature

In [56]:
print(final_df['Brand'].head(10000))  

0                                                                   [Dayco]
1                                                                  [Toyota]
2                                                                  [NISSAN]
3                                                 [Standard Motor Products]
4                                                                    [Febi]
5                                                                    [Febi]
6                                                       [USA Standard Gear]
7                                                   [National Seal/Bearing]
8                                                                [AC Delco]
9                                                             [MANN-FILTER]
10                                                                [NEW-APF]
11                                                                   [Ford]
12                                                                    [NGK]
13          

In [58]:
# Change all values in 'Brand' to uppercase
final_df['Brand'] = final_df['Brand'].apply(lambda x: [item.upper() for item in x] if isinstance(x, list) else x.upper())

# Convert "GM TRUCKS" to "GM TRUCK" in the 'Brand' column
final_df['Brand'] = final_df['Brand'].apply(lambda x: 'GM TRUCK' if x == 'GM TRUCKS' else x)

# Convert VOLKSWAGEN to VW
final_df['Brand'] = final_df['Brand'].apply(lambda x: 'VOLKSWAGEN' if x == 'VW' else x)

In [59]:
# Check if values in Year column are lists
brand_column_has_lists = final_df['Brand'].apply(lambda x: isinstance(x, list)).all()
print(f"'Brand' column contains only lists: {brand_column_has_lists}")

'Brand' column contains only lists: True


In [60]:
# Create an instance of multi-label binarizer
mlb = MultiLabelBinarizer()

# Create a DataFrame with one-hot encoded columns for the 'Brand' column
brand_df = pd.DataFrame(mlb.fit_transform(final_df['Brand']), columns=mlb.classes_, index=final_df.index)

# Add a prefix to the column names and replace spaces with underscores
brand_df.columns = 'BRAND_' + brand_df.columns.str.replace(' ', '_')


In [61]:
# Concatenate the one-hot encoded columns to the final DataFrame
final_one_hot_df = pd.concat([final_one_hot_df, brand_df], axis=1)

In [62]:
# Print the first few rows of the final DataFrame
print(final_one_hot_df.head(10))

   RECORD_ID  TYPE_  TYPE_12"_FAN_KIT  TYPE_12*_SEAL_VALVE_STEM  TYPE_2*12''FAN  TYPE_3-PRONG_THREE_CAVITY_MALE_TERMINAL_1_FEMALE_CONNECTOR  TYPE_3-WAY  TYPE_3.2L  TYPE_3.5L  TYPE_4_POLE  TYPE_4-PIN  TYPE_4-SPEED_AUTOMATIC_TRANSMISSION  TYPE_4WD  TYPE_4WD_SWITCH  TYPE_6-SPEED_MANUAL  TYPE_6-SPEED_NV5600_MANUAL_TRANSMISSION  TYPE_722  TYPE_74  TYPE_75W-90  TYPE_8691  TYPE_9  TYPE_90_DEGREE  TYPE_A  TYPE_AC_CONDENSER  TYPE_ACCESSORY_POWER_RELAY  TYPE_ACTUATOR  TYPE_ADAPTER  TYPE_AIR_COMPRESSOR_AC_BRACKET  TYPE_ALTERNATOR  TYPE_ALTERNATOR_BEARING  TYPE_ALTERNATOR_BRUSH_SET  TYPE_ALTERNATOR_CONNECTOR  TYPE_AMBIENT_AIR_TEMPERATURE_SENSOR_CONNECTOR  TYPE_ANTENNA  TYPE_ARD  TYPE_ARD_BLADE_FUSE  TYPE_ARD_FUSE  TYPE_ARD)  TYPE_AS_SHOWN_IN_THE_PICTURE  TYPE_AUTO  TYPE_AUTO_SHUT_DOWN_RELAY_CONNECTOR  TYPE_AUTO_TRANS_ACTUATOR_FEED_LIMIT_VALVE_PLUG_RETAINER  TYPE_AUTO_TRANS_DIPSTICK_TUBE  TYPE_AUTO_TRANS_DRAIN_PLUG  TYPE_AUTO_TRANS_OUTPUT_SHAFT_SPEED_SENSOR  TYPE_AUTO_TRANSMISSION_FILTER_KIT  \
0  

In [63]:
# Check if values in Year column are lists
year_column_has_lists = final_df['Year'].apply(lambda x: isinstance(x, list)).all()
print(f"'Year' column contains only lists: {year_column_has_lists}")

'Year' column contains only lists: True


## One-Hot encode the Year Column
This should be straight forward because the data was already formatted and prepped for one-hot encoding

In [64]:
# Convert elements in 'Year' column to strings
final_df['Year'] = final_df['Year'].apply(lambda x: [str(year) for year in x] if isinstance(x, list) else str(x))

In [65]:
# Initialize MultiLabelBinarizer
mlb = MultiLabelBinarizer()

# Create a DataFrame with one-hot encoded columns for the 'Year' column
year_df = pd.DataFrame(mlb.fit_transform(final_df['Year']), columns=mlb.classes_, index=final_df.index)

# Add a prefix to the column names
year_df = year_df.add_prefix('YEAR_')

In [66]:
# Remove the '8991' column
year_df.drop(columns=['YEAR_8991'], inplace=True)

# Concatenate the one-hot encoded columns to the final DataFrame
final_one_hot_df = pd.concat([final_one_hot_df, year_df], axis=1)

## Check the Fitment Column

In [67]:
# value counts of the 'Fitment' column
ftmnt_vc = final_df['Fitment'].value_counts()

print(ftmnt_vc.head(10))

Fitment
[]                                 3204
[Direct Replacement]                999
[No]                                 69
[Direct Replacement, No]             52
[Yes]                                32
[Direct Replacement, See Notes]      30
[Performance/Custom]                 27
[Direct Replacement, Yes]            12
[Ignition Coil]                      11
[Performance/Custom, No]              6
Name: count, dtype: int64


In [68]:
def clean_value(value):
    if isinstance(value, list):
        return [item.replace(';', '').replace('+', ',').replace('/', ',').replace('and', ',').replace(' & ', ', ') for item in value]
    elif isinstance(value, str):
        return value.replace(';', '').replace('+', ',').replace('/', ',').replace('and', ',').replace(' & ', ', ')
    else:
        return value
    
# Apply the function to the "Fitment" column
final_df['Fitment'] = final_df['Fitment'].apply(clean_value)

# Conver to string 
final_df['Fitment'] = final_df['Fitment'].apply(lambda x: ', '.join(x) if isinstance(x, list) else x)

# Replace ", " with ","
final_df['Fitment'] = final_df['Fitment'].str.replace(', ', ',')

# Convert back to list
final_df['Fitment'] = final_df['Fitment'].apply(lambda x: x.split(',') if isinstance(x, str) else x)

fitment_vc = final_df['Fitment'].value_counts()
print(fitment_vc.head(10000))

Fitment
[]                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [69]:
# MultiLabelBinarizer
mlb = MultiLabelBinarizer()

# Create a DataFrame with one-hot encoded columns for the 'Fitment' column
fitment_df = pd.DataFrame(mlb.fit_transform(final_df['Fitment']), columns=mlb.classes_, index=final_df.index)

# Keep Only columns that sum to more than 20
fitment_df = fitment_df.loc[:, fitment_df.sum() > 20]

# Change the Column Names to have "FTMNT_" in front and replace spaces with underscores
fitment_df.columns = ['FTMNT_' + col.replace(' ', '_') for col in fitment_df.columns]

# Concatenate the one-hot encoded columns to the final DataFrame
final_one_hot_df = pd.concat([final_one_hot_df, fitment_df], axis=1)

print(fitment_df.head(10))

   FTMNT_  FTMNT_Custom  FTMNT_Direct_Replacement  FTMNT_No  FTMNT_Performance  FTMNT_See_Notes  FTMNT_Yes
0       0             0                         1         0                  0                0          0
1       1             0                         0         0                  0                0          0
2       1             0                         0         0                  0                0          0
3       1             0                         0         0                  0                0          0
4       1             0                         0         0                  0                0          0
5       1             0                         0         0                  0                0          0
6       1             0                         0         0                  0                0          0
7       1             0                         0         0                  0                0          0
8       0             0              

## OEM Part Number is not even worth encoding

In [70]:
# One Hot Encode the OEM Part Number Column
# Check if values in OEM Part Number column are lists
oem_column_has_lists = final_df['OEM Part Number'].apply(lambda x: isinstance(x, list)).all()
print(f"'OEM Part Number' column contains only lists: {oem_column_has_lists}")

# value counts for the OEM Part Number and sort
final_df['OEM Part Number'].value_counts().sort_values(ascending=False).head(5)

'OEM Part Number' column contains only lists: True


OEM Part Number
[]                                2487
[n/a]                                7
[OEM]                                6
[Unknown]                            5
[DG-511, DG511, 3L3Z-12029-BA]       3
Name: count, dtype: int64

### Check Product Name Column

In [71]:
# Create One-Hot Encoded columns for the 'OEM Part Number' column
# Initialize MultiLabelBinarizer
mlb = MultiLabelBinarizer()

# Create a DataFrame with one-hot encoded columns for the 'OEM Part Number' column
product_name_df = pd.DataFrame(mlb.fit_transform(final_df['Product Name']), columns=mlb.classes_, index=final_df.index)

# Add a prefix to the column names and replace spaces with underscores
product_name_df.columns = 'PRODUCT_NAME_' + product_name_df.columns.str.replace(' ', '_')

# Concatenate the one-hot encoded columns to the final DataFrame
final_one_hot_df = pd.concat([final_one_hot_df, product_name_df], axis=1)

In [72]:
print(product_name_df.head(10))

   PRODUCT_NAME_4WD_Actuator  PRODUCT_NAME_4WD_Actuator_Valve  PRODUCT_NAME_4WD_Disconnect  PRODUCT_NAME_Alternator  PRODUCT_NAME_Alternator_Adapter_Plug  PRODUCT_NAME_Alternator_Bearing  PRODUCT_NAME_Alternator_Brush_Set  PRODUCT_NAME_Alternator_Connector  PRODUCT_NAME_Alternator_Decoupler_Pulley  PRODUCT_NAME_Alternator_Pulley  PRODUCT_NAME_Alternator_Rectifier_Set  PRODUCT_NAME_Auto_Trans_Accumulator_Piston_Seal  PRODUCT_NAME_Auto_Trans_Clutch_Housing_Input_Shaft_Bushing  PRODUCT_NAME_Auto_Trans_Clutch_Spring  PRODUCT_NAME_Auto_Trans_Connector  PRODUCT_NAME_Auto_Trans_Differential_Race  PRODUCT_NAME_Auto_Trans_Dipstick_Tube  PRODUCT_NAME_Auto_Trans_Drain_Plug_Gasket  PRODUCT_NAME_Auto_Trans_Electrical_Connecter_Seal  PRODUCT_NAME_Auto_Trans_Extension_Housing_Bearing  PRODUCT_NAME_Auto_Trans_Extension_Housing_Seal_Kit  PRODUCT_NAME_Auto_Trans_Filler_Tube  PRODUCT_NAME_Auto_Trans_Indicator_Light_Bulb  PRODUCT_NAME_Auto_Trans_Manual_Shaft_Seal  \
0                          0           

## Check the CATEGORY Column

In [73]:
# Value counts for the 'Category' column
category_vc = final_df['CATEGORY'].value_counts()

print(category_vc.head(10))

CATEGORY
0.0    1000
Name: count, dtype: int64


## CHeck the SKU Column

In [74]:
## Check the SKU Column
sku_vc = final_df['SKU'].value_counts()
print(sku_vc.head(10))

SKU
[]                                              2065
[Q112, 8412DE3E-EF1E-4D38-8CEB-3F1B3F5C6313]       1
[108812, 10232082]                                 1
[MOP:52104344AA]                                   1
[DBG194, 830757]                                   1
[164:632]                                          1
[227683]                                           1
[400:98635NX]                                      1
[400:52485KH]                                      1
[400:DK193YP]                                      1
Name: count, dtype: int64


## Check the Manufacturer Part Number


In [75]:
# Value
final_df['Manufacturer Part Number'].value_counts().sort_values(ascending=False).head(20)

Manufacturer Part Number
[]                                                                  868
[Does not apply]                                                     73
[Yes]                                                                12
[Does not apply, Does not apply]                                      9
[No]                                                                  8
[N/A]                                                                 6
[does not apply]                                                      6
[%20]                                                                 4
[DG-511]                                                              3
[Unknown, No]                                                         2
[9748B]                                                               2
[406, Yes]                                                            2
[Does not apply, No]                                                  2
[12670255]                             

In [76]:
# MultiLabelBinarizer
mlb = MultiLabelBinarizer()

# Create a DataFrame with one-hot encoded columns for the 'Manufacturer Part Number' column
mpn_df = pd.DataFrame(mlb.fit_transform(final_df['Manufacturer Part Number']), columns=mlb.classes_, index=final_df.index)

# Keep Only columns that sum to more than 20
mpn_df = mpn_df.loc[:, mpn_df.sum() > 20]

# Change the Column Names to have "MPN_" in front and replace spaces with underscores
mpn_df.columns = ['MPN_' + col.replace(' ', '_') for col in mpn_df.columns]

# Concatenate the one-hot encoded columns to the final DataFrame
print(mpn_df.head(10))

   MPN_Does_not_apply  MPN_Ignition_Coil  MPN_No  MPN_Yes
0                   0                  0       0        0
1                   0                  0       0        0
2                   0                  0       0        0
3                   0                  0       0        0
4                   0                  0       0        0
5                   0                  0       0        0
6                   0                  0       0        0
7                   0                  0       0        0
8                   0                  0       0        0
9                   0                  0       0        0


In [77]:
# Concatenate the one-hot encoded columns to the final DataFrame
final_one_hot_df = pd.concat([final_one_hot_df, mpn_df], axis=1)

# Keep this line as the last line. Exporting to CSV

In [78]:
# Rename "YEAR_" to "YEAR_NA"
final_one_hot_df.rename(columns={'YEAR_': 'YEAR_NA'}, inplace=True)

# Rename "FTMT_" to "FTMNT_NA"
final_one_hot_df.rename(columns={'FTMNT_': 'FTMNT_NA'}, inplace=True)

# Export the final DataFrame to a CSV file
final_one_hot_df.to_csv('final_one_hot_df.csv', index=False)

# Summarize the totals across each feature

In [79]:
# Summarize the totals across the columns
final_one_hot_df.sum().sort_values(ascending=False).head(2000)

RECORD_ID                                                                      12497500
MODEL_Other                                                                        3346
MAKE_Other                                                                         3291
FTMNT_NA                                                                           3205
TYPE_                                                                              2565
YEAR_NA                                                                            2363
FTMNT_Direct_Replacement                                                           1171
YEAR_2006                                                                           366
YEAR_2005                                                                           364
YEAR_2004                                                                           342
YEAR_2009                                                                           342
YEAR_2007                       